https://hub.xpub.nl/soupboat/~grgr/api/

# ... and I whish that your question has been answered


this tool includes two functions that intervene on text by replacing specific targeted words with either other words or single characters.
The 2 main functions are based in a very simple mechanism, but the scope and results one could get by using them in different ways and with different intentions can be very compelling.
One could break down the meaning of a text, by exposing its structure, taking out specific and meaningful words and detaching such text from its original context.
If then, these words would be substituted for others, the text can be given a new meaning, reclaiming concepts or ideas.
The words could be also erased and replaced for blank spaces in order to create a new narrative meaning with what is left on the page, as well as to create abstract compositions. 
This tool offers a broad spectrum of possibilities in which it can be used, from a very political and subversive use, to a more playful and artistic (or poetic) one.

### import

In [2]:
from flask import Flask, request, json, render_template, url_for, redirect
from jinja2 import Environment, PackageLoader, select_autoescape
from weasyprint import HTML, CSS
from nltk.tokenize import word_tokenize


import os 
import json

for the receipt printer:

In [3]:
from escpos.printer import Network


### functions

In [4]:
# function: respell
# '''replace all the occurrences of a targeted word in a given text'''
# def swap(text, target, replacement):
#     result = text.replace(target, replacement)
#     return result

def swap(text, target, replacement):
    target = target.lower()
    txt = word_tokenize(text)
    new = []
    
#     print(f"swap target:'{target}'")
    for w in txt:
        if w == target:
            w = replacement
            new = new + [w]
        elif w == target[0:1].upper() + target[1:]:
            w = replacement[0:1].upper() + replacement[1:] 
            new = new + [w]
        elif w == target.upper():
            w = replacement.upper()
            new = new + [w]
        else:
            new = new + [w]
    text = ' '.join(new)
    final= text.replace(' .','.').replace(' ,',',').replace(' :',':').replace(' ;',';').replace('< ','<').replace(' >','>').replace(' / ','/').replace('& ','&')
    return final

# function: stitch
# '''replace all the occurrences of a target word with a single character that is repeated as many times as the length of the target'''
## example: stitch('halo stitch this', 'this', '*') ----> result:'halo stitch ****'
def mend(text, target, replacement):
    target = target.lower()
    txt = word_tokenize(text)
    new = []
    
    for w in txt:
        if w == target:
            w = len(w)*replacement
            new = new + [w]
        elif w == target[0].upper() + target[1:]:
            w = len(w)*replacement
            new = new + [w]
        elif w== target.upper():
            w = len(w)*replacement 
            new = new + [w]
        else:
            new = new + [w]
    text = ' '.join(new)
    final= text.replace(' .','.').replace(' ,',',').replace(' :',':').replace(' ;',';').replace('< ','<').replace(' >','>').replace(' / ','/').replace('& ','&')
    return final


# reveal 
def underline(text,Group):
    txt = word_tokenize(text)
    
    txt_linebr = []
    for token in txt:
        if token == '<':
            continue
        elif token == 'br/':
            token='<br/>'
            txt_linebr.append(token)
        elif token == '>':
            continue
        else:
            txt_linebr.append(token)    
    new = []
    group = Group.split(",")
    for w in txt_linebr:
        if w=='<br/>':
            new = new + [w]
        elif w not in group:
            w = len(w) * ' '
            new = new + [w]
        elif w in group :
            new = new + [w]
    text = ' '.join(new)
    final= text.replace(' .','.').replace(' ,',',').replace(' :',':').replace(' ;',';').replace('< ','<').replace(' >','>').replace(' / ','/').replace('& ','&')
    return final

#function: txt_br
#to read the line breaks in a .txt file, returns string readable in html 
def txt_br(any_text):
    lines= any_text.readlines()
    replaced = ''
    for line in lines:
        replaced+= line.replace('\n', ' <br/> ')   
    return replaced

### flask 

!pwd
todo: adjust the width of the text on the right

In [ ]:
app = Flask(__name__)



# @app.route(f"/~grgr/api/")
# def replace():
    
#     text=request.values.get('text', '')
#     target = request.values.get('target', '')
#     replacement = request.values.get('replacement', '')
#     title = f"<h2>{request.values.get('title', '')}</h2>"
#     txt_result = f"<p>{swap(text, target, replacement)}</p>"
#     contents= title + txt_result
    
#     with open("./assets/outputs/db.txt", "a") as db:
#         db.write(contents+ " \n")
        
#     with open ("archive_section.html", "a") as output:
#         print(contents, file=output)
    
#     return render_template("index.html",
#                           text=text,
#                           contents=contents)


  

# archive page
@app.route(f"/~grgr/api/archive/", methods=['GET'])
def archive():
    with open("./assets/question.txt", 'r') as q_file:
        question = txt_br(q_file)
    #read the json file
    with open("archive.json", "r") as file:
            archive_input = json.loads(file.read())
            archive = archive_input['archive']
            answers=[]
#           # create a list with all the sections contents from the json
            for section in archive:
                answers.append(section['answers']) 
        
    return render_template("archive.html",
                           answers = answers,
                          question=question)



# main page with the form:
temp_changes=[]

@app.route("/~grgr/api/and_i_wish_that_your_question_has_been_answered/", methods=['GET', 'POST'])
def interact():
    target = request.values.get('target', '')
    f_replacement = request.values.get('f_replacement','')
    function = request.values.get('function', 'replace') 
    text = request.values.get('text','')
    result = ''
    
    with open("./assets/question.txt", 'r') as q_file:
        question = txt_br(q_file)
    
    with open("./assets/mitsotakis.txt", 'r') as file:
        source = txt_br(file)
   
    if request.method == 'POST':  
            if function == 'mend': 
                stitch = f_replacement
                if ' ' in stitch:
                    space = stitch.replace(' ','&nbsp; ')
                    result= mend(text, target, space)
                else:
                    result= mend(text, target, stitch)
            elif function == 'underline':
                popup =underline(source, target)
                result= popup.replace(' ','&nbsp; ')
            else:
                replacement = f_replacement
                result = swap(text, target, replacement)
                print('target is:'+ target)
            # now save temporary all the changes in the list changes
            temp_changes.append(result)

    if not text:
        # the first time we open the url the text is not saved, so plz flask, use the original source as text!
        if function == 'mend':
            result = mend(source, target, f_replacement)
        elif function== 'underline':
            popup = underline(source, target)
            result= popup.replace(' ','&nbsp; ')
            
        else:
            result = swap(source, target, f_replacement)
            
    print('result is:'+result)

    return render_template('postform.html', question=question, text=text, result=result, source= source, function=function, f_replacement=f_replacement)



#save the changes to the archive
@app.route("/~grgr/api/save/", methods=['GET', 'POST'])
def save_to_archive():
    if request.method == 'POST':
        
        with open("./assets/question.txt", 'r') as q_file:
            question = txt_br(q_file)
        
        with open("archive.json", "r") as file:
            archive_input = json.loads(file.read())
            archive = archive_input['archive']
            i = len(temp_changes)-1
            while i >= 0:
                last_change = temp_changes[i]
                if last_change:
                    last_change= temp_changes[i]
                    
                    section = {"question":question, 
                       "answers": last_change}
                    archive.append(section)
                    print('saved')
                    break
                else:
                    i = i-1  
            
        #print to the archive    
        with open("archive.json", "w") as file:
            file.write(json.dumps({"archive":archive}))
            
        #print with the line printer 
#         with open('/dev/usb/lp0', 'w') as lp:
#             print(last_change, file=lp) 
#             print_last = last_change.replace('&nbsp; ',' ').replace('<br/>', '\n')
#             print(f'last print is:{print_last}')
        
        #for ethernet receipt printer
#         kitchen = Network("192.168.1.140") #Printer IP Address
#         kitchen.text(print_last) 
        
#         temp_changes.clear()iii
             
    return redirect("https://hub.xpub.nl/soupboat/~grgr/api/and_i_wish_that_your_question_has_been_answered/")

app.run(port=9087)

 * Serving Flask app '__main__' (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:9087/ (Press CTRL+C to quit)
127.0.0.1 - - [17/Dec/2021 11:43:28] "GET /~grgr/api/and_i_wish_that_your_question_has_been_answered/ HTTP/1.0" 200 -


result is:KYRIAKOS MITSOTAKIS, GREEK PRIME MINISTER <br/> <br/> I understand that in the Netherlands you have a culture of asking direct questions to politicians, which I very much respect. <br/> What I will not accept is that, in this office, you will insult me, or the Greek people, with accusations and expressions that are not supported by material facts when this country has been dealing with a migration crisis of unprecedented intensity, has been saving hundreds, if not thousands of people at sea. <br/> We just rescued 250 people in danger of drowning south of Crete, we are doing this every single day rescuing people at sea, while, at the same time, we are intercepting boats that come from Turkey, as we have the right to do in accordance with European regulations and waiting for the Turkish Coast Guard to come and pick them up and return them to Turkey. <br/> So, rather than putting the blame on Greece, you should put the blame on those who have been instrumentalizing migration sys

127.0.0.1 - - [17/Dec/2021 11:43:31] "GET /~grgr/api/archive/ HTTP/1.0" 200 -


In [48]:
temp= ['']
print(len(temp))

1


# 

## teeeeeesstttssssss

In [5]:
from weasyprint import HTML, CSS

# with is nice cause it auto-closes the file once "outside" the with block
with open ("test.html", "a") as output:
    print ("<pre>", file=output)
    print (sent + " ", file=output)
    print ("</pre>", file=output)
HTML(filename="test.html").write_pdf('./test.pdf')

In [106]:
def ifcap(text, target, replacement):
    result=[]
    index= 0
    for w in text.split():
        w_lower = w.lower()
        if w_lower == target and w.isupper()==true:
            while w[index].isupper() == true and index<len(w):
                change=''
                for l in replacement:
                    change= l.upper()
                index +=1
            result += [w_lower.replace(target, replacement)]
    print(result)

In [128]:
def ifcap(text, target, replacement):
    result=[]
    index= 0
    for w in text.split():
        w_lower = w.lower()
        change=''
        if w_lower == target:
            
            while index < len(w):
                print('oo')
#                 if str(w[index]).isupper() == true:
#                     change+= str(replacement[index]).upper()
#                     print (change)
#                 else:
#                     change+= replacement[index]
                index+=1
        result += [w_lower.replace(target, change)]
    print(result)

In [129]:
ifcap('Capital and capital', 'c', 'CC')

['apital', 'and', 'apital']


In [130]:
word ='ciao'
print(len(word))

4


In [13]:
with open("./assets/mitsotakis.txt", 'r') as source:
    print(source)

<_io.TextIOWrapper name='./assets/mitsotakis.txt' mode='r' encoding='UTF-8'>


In [44]:
sentence= "stitches //Have something <\repairing\ have HAVE"

In [17]:
# stitch function, replace a target with stitches

def change(text, target, replacement):
    result = text.replace(target, replacement)
    return result

In [30]:
#updated swap function!
from nltk.tokenize import word_tokenize

def stitch(text, target, replacement):
    target = target.lower()
    txt = word_tokenize(text)
    new = []
    
    for w in txt:
        if w == target:
            w = len(w)*replacement
            new = new + [w]
        elif w == target[0].upper() + target[1:]:
            w = len(w)*replacement
            new = new + [w]
        elif w== target.upper():
            w = len(w)*replacement 
            new = new + [w]
        else:
            new = new + [w]
    text = ' '.join(new)
    return text

In [54]:
mend(sentence, 'have', ' ')

'stitches //Have something <epairing\\          '

In [15]:
source = 'ciao come va'

In [16]:
print(source.index('ciao'))

0
